In [17]:
import numpy as np
#import torch 

data = open("PatientDetect.txt", "r")

tdata = np.empty((0,24),dtype=float)
tlabel = np.empty((0,3),dtype=float)
for d in data.readlines():
    tdata = np.append(tdata, np.array([float(t) for t in d.split(",")[:24]]).reshape((1,24)), axis=0 )
    labelNum = float(d.split(",")[24].strip("\n"))
    labelV = np.zeros((3,1))
    labelV[int(labelNum)] = 1
    tlabel = np.append(tlabel, labelV.reshape(1,3), axis=0)
    
print(tdata)
print(tlabel)

[[  0.   0.   0. ... 966. 954. 958.]
 [ 15.  34.  11. ... 952. 939. 951.]
 [ 77.  19.   0. ... 944. 952. 957.]
 ...
 [ -8.  -1.   4. ... 962. 955. 959.]
 [ 36.   1.   3. ... 963. 950. 929.]
 [  9.   6.  10. ... 956. 948. 959.]]
[[1. 0. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [1. 0. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0.

In [26]:
#isBody predictor
import keras
import pickle
from keras.optimizers import Adam,SGD 
from keras.models import Sequential
from sklearn.model_selection import train_test_split
from keras.layers import Dense
# Neural network

X_train, x_test, y_train, y_test = train_test_split(tdata, tlabel, test_size=0.05, random_state=80)

model = Sequential()
model.add(Dense(12, input_dim=24,kernel_initializer='normal', activation='linear'))
#model.add(Dense(24, kernel_initializer='normal', activation='linear'))
model.add(Dense(6, kernel_initializer='normal',activation='linear'))
model.add(Dense(3, kernel_initializer='normal',activation='sigmoid'))
#model.add(Dense(1, kernel_initializer='normal',activation='linear'))

opt = Adam(lr=0.0001)#, beta_1=0.9, beta_2=0.999, epsilon=None, decay=0.0, amsgrad=False)#adam also does the same but gives better accuracy initially 90.08 or 90.11
model.compile(loss=['binary_crossentropy'], 
              optimizer=opt, 
              metrics=['accuracy'])

history = model.fit(X_train, y_train, epochs=2000,validation_split=0.2, batch_size=64)

print(model.evaluate(X_train, y_train)[1])
predictions=model.predict(tdata, batch_size=300, verbose=1)

tot = 0
corr = 0
print("linear linear")
for i in range(len(tlabel)):
    print(predictions[i],tlabel[i])
    #print(tlabel[i].size)
    print(".....")
    maxPos = np.argmax(predictions[i])
    predLabel = np.zeros((1,3), dtype=float)
    corrLabel = np.zeros((1,3), dtype=float)
    predLabel[0][maxPos] = 1.0
    #corrLabel[0][int(tlabel[i])] = 1.0
    
    if(np.array_equal(tlabel[i].reshape(1,3), predLabel)):
        corr += 1
    tot += 1
    
print("Correct " + str(corr) + " , Total " + str(tot) + " , Accuracy " + str(corr/tot))
model.save('isBody_predictor.h5')

Train on 140 samples, validate on 35 samples
Epoch 1/2000
140/140 [==============================] - 0s 3ms/step - loss: 1.1680 - accuracy: 0.3333 - val_loss: 1.1178 - val_accuracy: 0.3333
Epoch 2/2000
140/140 [==============================] - 0s 143us/step - loss: 1.0751 - accuracy: 0.3333 - val_loss: 1.0241 - val_accuracy: 0.3333
Epoch 3/2000
140/140 [==============================] - 0s 93us/step - loss: 0.9928 - accuracy: 0.3333 - val_loss: 0.9390 - val_accuracy: 0.3905
Epoch 4/2000
140/140 [==============================] - 0s 93us/step - loss: 0.9181 - accuracy: 0.4024 - val_loss: 0.8656 - val_accuracy: 0.3714
Epoch 5/2000
140/140 [==============================] - 0s 107us/step - loss: 0.8570 - accuracy: 0.4119 - val_loss: 0.8046 - val_accuracy: 0.4190
Epoch 6/2000
140/140 [==============================] - 0s 171us/step - loss: 0.8084 - accuracy: 0.4452 - val_loss: 0.7573 - val_accuracy: 0.5905
Epoch 7/2000
140/140 [==============================] - 0s 114us/step - loss: 0.771

Epoch 56/2000
140/140 [==============================] - 0s 93us/step - loss: 0.6162 - accuracy: 0.6667 - val_loss: 0.5905 - val_accuracy: 0.6667
Epoch 57/2000
140/140 [==============================] - 0s 107us/step - loss: 0.6161 - accuracy: 0.6667 - val_loss: 0.5905 - val_accuracy: 0.6667
Epoch 58/2000
140/140 [==============================] - 0s 100us/step - loss: 0.6159 - accuracy: 0.6667 - val_loss: 0.5906 - val_accuracy: 0.6667
Epoch 59/2000
140/140 [==============================] - 0s 129us/step - loss: 0.6158 - accuracy: 0.6667 - val_loss: 0.5903 - val_accuracy: 0.6667
Epoch 60/2000
140/140 [==============================] - 0s 100us/step - loss: 0.6156 - accuracy: 0.6667 - val_loss: 0.5906 - val_accuracy: 0.6667
Epoch 61/2000
140/140 [==============================] - 0s 114us/step - loss: 0.6155 - accuracy: 0.6667 - val_loss: 0.5905 - val_accuracy: 0.6667
Epoch 62/2000
140/140 [==============================] - 0s 114us/step - loss: 0.6153 - accuracy: 0.6667 - val_loss: 0.

140/140 [==============================] - 0s 93us/step - loss: 0.6081 - accuracy: 0.6667 - val_loss: 0.5835 - val_accuracy: 0.6667
Epoch 112/2000
140/140 [==============================] - 0s 114us/step - loss: 0.6075 - accuracy: 0.6667 - val_loss: 0.5816 - val_accuracy: 0.6667
Epoch 113/2000
140/140 [==============================] - 0s 114us/step - loss: 0.6075 - accuracy: 0.6667 - val_loss: 0.5796 - val_accuracy: 0.6667
Epoch 114/2000
140/140 [==============================] - 0s 107us/step - loss: 0.6076 - accuracy: 0.6667 - val_loss: 0.5783 - val_accuracy: 0.6667
Epoch 115/2000
140/140 [==============================] - 0s 114us/step - loss: 0.6074 - accuracy: 0.6667 - val_loss: 0.5774 - val_accuracy: 0.6667
Epoch 116/2000
140/140 [==============================] - 0s 107us/step - loss: 0.6073 - accuracy: 0.6667 - val_loss: 0.5774 - val_accuracy: 0.6667
Epoch 117/2000
140/140 [==============================] - 0s 114us/step - loss: 0.6069 - accuracy: 0.6667 - val_loss: 0.5786 - v

140/140 [==============================] - 0s 100us/step - loss: 0.5967 - accuracy: 0.6667 - val_loss: 0.5683 - val_accuracy: 0.6667
Epoch 167/2000
140/140 [==============================] - 0s 79us/step - loss: 0.5965 - accuracy: 0.6667 - val_loss: 0.5689 - val_accuracy: 0.6667
Epoch 168/2000
140/140 [==============================] - 0s 100us/step - loss: 0.5961 - accuracy: 0.6667 - val_loss: 0.5694 - val_accuracy: 0.6667
Epoch 169/2000
140/140 [==============================] - 0s 93us/step - loss: 0.5956 - accuracy: 0.6667 - val_loss: 0.5708 - val_accuracy: 0.6667
Epoch 170/2000
140/140 [==============================] - 0s 107us/step - loss: 0.5956 - accuracy: 0.6667 - val_loss: 0.5729 - val_accuracy: 0.6667
Epoch 171/2000
140/140 [==============================] - 0s 114us/step - loss: 0.5954 - accuracy: 0.6667 - val_loss: 0.5734 - val_accuracy: 0.6667
Epoch 172/2000
140/140 [==============================] - 0s 129us/step - loss: 0.5952 - accuracy: 0.6667 - val_loss: 0.5721 - va

140/140 [==============================] - 0s 114us/step - loss: 0.5749 - accuracy: 0.6667 - val_loss: 0.5449 - val_accuracy: 0.6667
Epoch 222/2000
140/140 [==============================] - 0s 93us/step - loss: 0.5741 - accuracy: 0.6667 - val_loss: 0.5452 - val_accuracy: 0.6667
Epoch 223/2000
140/140 [==============================] - 0s 93us/step - loss: 0.5733 - accuracy: 0.6667 - val_loss: 0.5448 - val_accuracy: 0.6667
Epoch 224/2000
140/140 [==============================] - 0s 100us/step - loss: 0.5727 - accuracy: 0.6667 - val_loss: 0.5452 - val_accuracy: 0.6667
Epoch 225/2000
140/140 [==============================] - 0s 107us/step - loss: 0.5719 - accuracy: 0.6667 - val_loss: 0.5449 - val_accuracy: 0.6667
Epoch 226/2000
140/140 [==============================] - 0s 107us/step - loss: 0.5717 - accuracy: 0.6667 - val_loss: 0.5438 - val_accuracy: 0.6667
Epoch 227/2000
140/140 [==============================] - 0s 100us/step - loss: 0.5705 - accuracy: 0.6667 - val_loss: 0.5434 - va

...

140/140 [==============================] - 0s 86us/step - loss: 0.2079 - accuracy: 0.8929 - val_loss: 0.1812 - val_accuracy: 0.9048
Epoch 1810/2000
140/140 [==============================] - 0s 93us/step - loss: 0.2120 - accuracy: 0.9000 - val_loss: 0.1806 - val_accuracy: 0.9143
Epoch 1811/2000
140/140 [==============================] - 0s 100us/step - loss: 0.2147 - accuracy: 0.9048 - val_loss: 0.1808 - val_accuracy: 0.9143
Epoch 1812/2000
140/140 [==============================] - 0s 79us/step - loss: 0.2122 - accuracy: 0.9000 - val_loss: 0.1827 - val_accuracy: 0.9143
Epoch 1813/2000
140/140 [==============================] - 0s 93us/step - loss: 0.2081 - accuracy: 0.9048 - val_loss: 0.1933 - val_accuracy: 0.9238
Epoch 1814/2000
140/140 [==============================] - 0s 114us/step - loss: 0.2103 - accuracy: 0.8952 - val_loss: 0.2060 - val_accuracy: 0.9048
Epoch 1815/2000
140/140 [==============================] - 0s 107us/step - loss: 0.2149 - accuracy: 0.9000 - val_loss: 0.2065 

140/140 [==============================] - 0s 86us/step - loss: 0.2073 - accuracy: 0.9119 - val_loss: 0.1889 - val_accuracy: 0.9238
Epoch 1865/2000
140/140 [==============================] - 0s 107us/step - loss: 0.2077 - accuracy: 0.9071 - val_loss: 0.1883 - val_accuracy: 0.9238
Epoch 1866/2000
140/140 [==============================] - 0s 200us/step - loss: 0.2075 - accuracy: 0.9071 - val_loss: 0.1857 - val_accuracy: 0.9143
Epoch 1867/2000
140/140 [==============================] - 0s 93us/step - loss: 0.2076 - accuracy: 0.9024 - val_loss: 0.1840 - val_accuracy: 0.9143
Epoch 1868/2000
140/140 [==============================] - 0s 107us/step - loss: 0.2074 - accuracy: 0.9048 - val_loss: 0.1846 - val_accuracy: 0.9143
Epoch 1869/2000
140/140 [==============================] - 0s 93us/step - loss: 0.2072 - accuracy: 0.8952 - val_loss: 0.1853 - val_accuracy: 0.9143
Epoch 1870/2000
140/140 [==============================] - 0s 86us/step - loss: 0.2074 - accuracy: 0.8929 - val_loss: 0.1855 

140/140 [==============================] - 0s 121us/step - loss: 0.2079 - accuracy: 0.8976 - val_loss: 0.1822 - val_accuracy: 0.9048
Epoch 1920/2000
140/140 [==============================] - 0s 321us/step - loss: 0.2089 - accuracy: 0.9000 - val_loss: 0.1820 - val_accuracy: 0.9048
Epoch 1921/2000
140/140 [==============================] - 0s 228us/step - loss: 0.2084 - accuracy: 0.8952 - val_loss: 0.1842 - val_accuracy: 0.9143
Epoch 1922/2000
140/140 [==============================] - 0s 107us/step - loss: 0.2081 - accuracy: 0.8976 - val_loss: 0.1887 - val_accuracy: 0.9238
Epoch 1923/2000
140/140 [==============================] - 0s 121us/step - loss: 0.2072 - accuracy: 0.8976 - val_loss: 0.1897 - val_accuracy: 0.9238
Epoch 1924/2000
140/140 [==============================] - 0s 100us/step - loss: 0.2077 - accuracy: 0.9000 - val_loss: 0.1888 - val_accuracy: 0.9238
Epoch 1925/2000
140/140 [==============================] - 0s 129us/step - loss: 0.2074 - accuracy: 0.9048 - val_loss: 0.1

140/140 [==============================] - 0s 100us/step - loss: 0.2099 - accuracy: 0.9000 - val_loss: 0.1943 - val_accuracy: 0.9238
Epoch 1975/2000
140/140 [==============================] - 0s 114us/step - loss: 0.2087 - accuracy: 0.9000 - val_loss: 0.1898 - val_accuracy: 0.9238
Epoch 1976/2000
140/140 [==============================] - 0s 107us/step - loss: 0.2075 - accuracy: 0.9000 - val_loss: 0.1867 - val_accuracy: 0.9143
Epoch 1977/2000
140/140 [==============================] - 0s 107us/step - loss: 0.2064 - accuracy: 0.8976 - val_loss: 0.1839 - val_accuracy: 0.9143
Epoch 1978/2000
140/140 [==============================] - 0s 114us/step - loss: 0.2071 - accuracy: 0.9000 - val_loss: 0.1828 - val_accuracy: 0.9238
Epoch 1979/2000
140/140 [==============================] - 0s 114us/step - loss: 0.2086 - accuracy: 0.8976 - val_loss: 0.1841 - val_accuracy: 0.9238
Epoch 1980/2000
140/140 [==============================] - 0s 114us/step - loss: 0.2081 - accuracy: 0.9024 - val_loss: 0.1

[0.00211422 0.49596676 0.09591669] [0. 1. 0.]
.....
[3.8010225e-04 4.6362090e-01 2.0304623e-01] [0. 1. 0.]
.....
[1.3673652e-04 8.3539659e-01 3.3490267e-02] [0. 1. 0.]
.....
[5.2873718e-05 9.0403438e-01 2.6930474e-02] [0. 1. 0.]
.....
[0.00487043 0.0890459  0.68735135] [0. 0. 1.]
.....
[0.00116571 0.07276593 0.8379861 ] [0. 0. 1.]
.....
[0.00077236 0.16213538 0.6307077 ] [0. 0. 1.]
.....
[4.490924e-04 1.700645e-01 5.603141e-01] [0. 0. 1.]
.....
[2.0678119e-04 2.7690426e-01 4.5354575e-01] [0. 0. 1.]
.....
[2.0083004e-04 5.0183100e-01 1.7143865e-01] [0. 0. 1.]
.....
[4.2794266e-08 5.0483257e-01 8.4298486e-01] [0. 1. 0.]
.....
[3.0088458e-08 9.9257046e-01 8.8503910e-03] [0. 1. 0.]
.....
[9.5090563e-08 9.8387873e-01 2.7845031e-02] [0. 1. 0.]
.....
[2.3435895e-09 8.5844636e-01 6.2961429e-01] [0. 1. 0.]
.....
[1.3339123e-08 9.9706751e-01 3.8211572e-03] [0. 1. 0.]
.....
[3.5627790e-10 9.9835384e-01 1.0700742e-02] [0. 1. 0.]
.....
[8.6615376e-10 9.9956077e-01 8.7099418e-04] [0. 1. 0.]
.....
[5

In [10]:
import numpy as np
#import torch 

data = open("PatientWeight.txt", "r")

tdata = np.empty((0,24),dtype=float)
tlabel = np.empty((0,1),dtype=float)
for d in data.readlines():
    tdata = np.append(tdata, np.array([float(t) for t in d.split(",")[:24]]).reshape((1,24)), axis=0 )
    tlabel = np.append(tlabel, np.array([float(d.split(",")[24].strip("\n"))]).reshape(1,1) ,axis=0)
    
print(tdata)
print(tlabel)

[[  7.  49.   8. ... 959. 934. 955.]
 [  7.  49.   8. ... 958. 934. 956.]
 [  1.   9.  33. ... 965. 947. 946.]
 ...
 [ 22.  22.  14. ... 961. 940. 951.]
 [ -2.  10.   0. ... 967. 953. 954.]
 [  1.  22.   1. ... 967. 938. 946.]]
[[72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [57.]
 [57.]
 [57.]
 [57.]
 [57.]
 [57.]
 [57.]
 [57.]
 [57.]
 [55.]
 [55.]
 [55.]
 [55.]
 [55.]
 [55.]
 [55.]
 [55.]
 [55.]
 [55.]
 [55.]
 [67.]
 [67.]
 [67.]
 [67.]
 [67.]
 [67.]
 [67.]
 [72.]
 [72.]
 [72.]
 [78.]
 [78.]
 [78.]
 [40.]
 [40.]
 [40.]
 [40.]
 [48.]
 [48.]
 [48.]
 [48.]
 [57.]
 [57.]
 [57.]
 [55.]
 [55.]
 [55.]]


In [ ]:
#isWeight predictor
import keras
import pickle
import tensorflow as tf
from keras.optimizers import Adam,SGD 
from keras.models import Sequential
from sklearn.model_selection import train_test_split
from keras.layers import Dense

#def L2_Loss(y_true, y_pred):
#    return tf.math_sqrt(tf.reduce_sum(tf.square(y_true - y_pred)))

# Neural network

X_train, x_test, y_train, y_test = train_test_split(tdata, tlabel, test_size=0.05, random_state=80)

print(y_train)

model = Sequential()
model.add(Dense(48, input_dim=24,kernel_initializer='normal', activation='relu'))
model.add(Dense(24, kernel_initializer='normal', activation='relu'))
model.add(Dense(12, kernel_initializer='normal',activation='relu'))
model.add(Dense(6, kernel_initializer='normal',activation='relu'))
model.add(Dense(1, kernel_initializer='normal',activation='linear'))

opt = Adam(lr=0.0001)#, beta_1=0.9, beta_2=0.999, epsilon=None, decay=0.0, amsgrad=False)#adam also does the same but gives better accuracy initially 90.08 or 90.11
model.compile(loss="MSE", 
              optimizer=opt, 
              metrics=['accuracy'])

history = model.fit(X_train, y_train, epochs=50000,validation_split=0.2, batch_size=64)

print(model.evaluate(X_train, y_train)[1])
predictions=model.predict(tdata, batch_size=300, verbose=1)

tot = 0
corr = 0
print("linear linear")
for i in range(len(tlabel)):
    print(predictions[i][0],tlabel[i][0])
    if (predictions[i][0] >= 0.5 and tlabel[i][0] == 1):
        corr = corr + 1
    elif (predictions[i][0] < 0.5 and tlabel[i][0] == 0):
        corr = corr + 1
    tot = tot + 1
    
print("Correct " + str(corr) + " , Total " + str(tot) + " , Accuracy " + str(corr/tot))
model.save('isBodyWeigth_predictor.h5')

[[67.]
 [78.]
 [57.]
 [48.]
 [72.]
 [48.]
 [57.]
 [72.]
 [78.]
 [78.]
 [72.]
 [72.]
 [72.]
 [55.]
 [40.]
 [48.]
 [72.]
 [72.]
 [40.]
 [55.]
 [40.]
 [55.]
 [57.]
 [67.]
 [48.]
 [55.]
 [78.]
 [55.]
 [40.]
 [40.]
 [40.]
 [48.]
 [40.]
 [67.]
 [78.]
 [55.]
 [48.]
 [48.]
 [55.]
 [48.]
 [72.]
 [67.]
 [55.]
 [48.]
 [40.]
 [78.]
 [40.]
 [57.]
 [55.]
 [40.]
 [57.]
 [72.]
 [72.]
 [55.]
 [55.]
 [40.]
 [40.]
 [57.]
 [40.]
 [78.]
 [78.]
 [78.]
 [57.]
 [48.]
 [55.]
 [67.]
 [72.]
 [72.]
 [78.]
 [57.]
 [57.]
 [72.]
 [78.]
 [72.]
 [67.]
 [72.]
 [40.]
 [40.]
 [72.]
 [57.]
 [72.]
 [48.]
 [78.]
 [55.]
 [57.]]
Train on 68 samples, validate on 17 samples
Epoch 1/50000
68/68 [==============================] - 1s 13ms/step - loss: 3582.0989 - acc: 0.0000e+00 - val_loss: 4146.6040 - val_acc: 0.0000e+00
Epoch 2/50000
68/68 [==============================] - 0s 205us/step - loss: 3579.6064 - acc: 0.0000e+00 - val_loss: 4144.0205 - val_acc: 0.0000e+00
Epoch 3/50000
68/68 [==============================] - 0s 220us

68/68 [==============================] - 0s 176us/step - loss: 3536.2231 - acc: 0.0000e+00 - val_loss: 4097.5005 - val_acc: 0.0000e+00
Epoch 106/50000
68/68 [==============================] - 0s 161us/step - loss: 3534.2923 - acc: 0.0000e+00 - val_loss: 4095.3323 - val_acc: 0.0000e+00
Epoch 107/50000
68/68 [==============================] - 0s 176us/step - loss: 3532.2825 - acc: 0.0000e+00 - val_loss: 4092.9573 - val_acc: 0.0000e+00
Epoch 108/50000
68/68 [==============================] - 0s 176us/step - loss: 3530.0859 - acc: 0.0000e+00 - val_loss: 4090.4485 - val_acc: 0.0000e+00
Epoch 109/50000
68/68 [==============================] - 0s 176us/step - loss: 3527.7469 - acc: 0.0000e+00 - val_loss: 4087.7256 - val_acc: 0.0000e+00
Epoch 110/50000
68/68 [==============================] - 0s 176us/step - loss: 3525.2409 - acc: 0.0000e+00 - val_loss: 4084.8098 - val_acc: 0.0000e+00
Epoch 111/50000
68/68 [==============================] - 0s 161us/step - loss: 3522.5699 - acc: 0.0000e+00 - v

68/68 [==============================] - 0s 147us/step - loss: 279.3188 - acc: 0.1471 - val_loss: 359.1997 - val_acc: 0.0000e+00
Epoch 214/50000
68/68 [==============================] - 0s 161us/step - loss: 261.4531 - acc: 0.0000e+00 - val_loss: 335.0268 - val_acc: 0.0000e+00
Epoch 215/50000
68/68 [==============================] - 0s 191us/step - loss: 246.0374 - acc: 0.0000e+00 - val_loss: 313.3191 - val_acc: 0.0000e+00
Epoch 216/50000
68/68 [==============================] - 0s 191us/step - loss: 232.5246 - acc: 0.0000e+00 - val_loss: 294.2004 - val_acc: 0.0000e+00
Epoch 217/50000
68/68 [==============================] - 0s 191us/step - loss: 221.1786 - acc: 0.0000e+00 - val_loss: 277.5405 - val_acc: 0.0000e+00
Epoch 218/50000
68/68 [==============================] - 0s 176us/step - loss: 211.5117 - acc: 0.0000e+00 - val_loss: 262.9349 - val_acc: 0.0000e+00
Epoch 219/50000
68/68 [==============================] - 0s 191us/step - loss: 203.3763 - acc: 0.0000e+00 - val_loss: 249.6021

68/68 [==============================] - 0s 176us/step - loss: 172.6438 - acc: 0.0000e+00 - val_loss: 177.9860 - val_acc: 0.0000e+00
Epoch 324/50000
68/68 [==============================] - 0s 191us/step - loss: 172.6877 - acc: 0.0000e+00 - val_loss: 178.8520 - val_acc: 0.0000e+00
Epoch 325/50000
68/68 [==============================] - 0s 161us/step - loss: 172.6745 - acc: 0.0000e+00 - val_loss: 179.1243 - val_acc: 0.0000e+00
Epoch 326/50000
68/68 [==============================] - 0s 161us/step - loss: 172.6702 - acc: 0.0000e+00 - val_loss: 178.9621 - val_acc: 0.0000e+00
Epoch 327/50000
68/68 [==============================] - 0s 161us/step - loss: 172.6511 - acc: 0.0000e+00 - val_loss: 178.4321 - val_acc: 0.0000e+00
Epoch 328/50000
68/68 [==============================] - 0s 161us/step - loss: 172.6233 - acc: 0.0000e+00 - val_loss: 177.5975 - val_acc: 0.0000e+00
Epoch 329/50000
68/68 [==============================] - 0s 147us/step - loss: 172.5611 - acc: 0.0000e+00 - val_loss: 176.

68/68 [==============================] - 0s 191us/step - loss: 172.6279 - acc: 0.0000e+00 - val_loss: 183.4457 - val_acc: 0.0000e+00
Epoch 379/50000
68/68 [==============================] - 0s 161us/step - loss: 172.8142 - acc: 0.0294 - val_loss: 183.5390 - val_acc: 0.0000e+00
Epoch 380/50000
68/68 [==============================] - 0s 176us/step - loss: 172.8090 - acc: 0.0294 - val_loss: 183.4857 - val_acc: 0.0000e+00
Epoch 381/50000
68/68 [==============================] - 0s 161us/step - loss: 172.7507 - acc: 0.0294 - val_loss: 183.8161 - val_acc: 0.0000e+00
Epoch 382/50000
68/68 [==============================] - 0s 176us/step - loss: 172.7638 - acc: 0.0294 - val_loss: 183.7735 - val_acc: 0.0000e+00
Epoch 383/50000
68/68 [==============================] - 0s 161us/step - loss: 172.7538 - acc: 0.0294 - val_loss: 183.8385 - val_acc: 0.0000e+00
Epoch 384/50000
68/68 [==============================] - 0s 147us/step - loss: 172.7545 - acc: 0.0294 - val_loss: 184.3472 - val_acc: 0.1765
E

...

68/68 [==============================] - 0s 176us/step - loss: 19.0715 - acc: 0.1029 - val_loss: 82.9778 - val_acc: 0.0000e+00
Epoch 40220/50000
68/68 [==============================] - 0s 205us/step - loss: 20.0513 - acc: 0.1618 - val_loss: 82.3496 - val_acc: 0.0000e+00
Epoch 40221/50000
68/68 [==============================] - 0s 191us/step - loss: 20.4413 - acc: 0.1324 - val_loss: 82.9337 - val_acc: 0.0000e+00
Epoch 40222/50000
68/68 [==============================] - 0s 161us/step - loss: 19.6422 - acc: 0.1471 - val_loss: 85.3697 - val_acc: 0.0000e+00
Epoch 40223/50000
68/68 [==============================] - 0s 176us/step - loss: 18.8537 - acc: 0.0882 - val_loss: 89.2210 - val_acc: 0.0000e+00
Epoch 40224/50000
68/68 [==============================] - 0s 191us/step - loss: 19.0793 - acc: 0.0588 - val_loss: 91.6359 - val_acc: 0.0000e+00
Epoch 40225/50000
68/68 [==============================] - 0s 191us/step - loss: 19.5823 - acc: 0.0441 - val_loss: 90.6485 - val_acc: 0.0000e+00
Epo

68/68 [==============================] - 0s 161us/step - loss: 19.2791 - acc: 0.0588 - val_loss: 87.2855 - val_acc: 0.0000e+00
Epoch 40332/50000
68/68 [==============================] - 0s 176us/step - loss: 19.1352 - acc: 0.0588 - val_loss: 84.5161 - val_acc: 0.0000e+00
Epoch 40333/50000
68/68 [==============================] - 0s 161us/step - loss: 18.9501 - acc: 0.0735 - val_loss: 81.9402 - val_acc: 0.0000e+00
Epoch 40334/50000
68/68 [==============================] - 0s 176us/step - loss: 19.3656 - acc: 0.1029 - val_loss: 80.8912 - val_acc: 0.0000e+00
Epoch 40335/50000
68/68 [==============================] - 0s 161us/step - loss: 19.9078 - acc: 0.1029 - val_loss: 80.5491 - val_acc: 0.0000e+00
Epoch 40336/50000
68/68 [==============================] - 0s 176us/step - loss: 20.1285 - acc: 0.1176 - val_loss: 80.4008 - val_acc: 0.0000e+00
Epoch 40337/50000
68/68 [==============================] - 0s 205us/step - loss: 20.1712 - acc: 0.1176 - val_loss: 80.4399 - val_acc: 0.0000e+00
Epo

Epoch 40444/50000
68/68 [==============================] - 0s 205us/step - loss: 18.5208 - acc: 0.0441 - val_loss: 87.1253 - val_acc: 0.0000e+00
Epoch 40445/50000
68/68 [==============================] - 0s 161us/step - loss: 18.2712 - acc: 0.0441 - val_loss: 85.0191 - val_acc: 0.0000e+00
Epoch 40446/50000
68/68 [==============================] - 0s 205us/step - loss: 18.1338 - acc: 0.0882 - val_loss: 83.7336 - val_acc: 0.0000e+00
Epoch 40447/50000
68/68 [==============================] - 0s 176us/step - loss: 18.1689 - acc: 0.0735 - val_loss: 82.9716 - val_acc: 0.0000e+00
Epoch 40448/50000
68/68 [==============================] - 0s 205us/step - loss: 18.3357 - acc: 0.0588 - val_loss: 81.5825 - val_acc: 0.0000e+00
Epoch 40449/50000
68/68 [==============================] - 0s 205us/step - loss: 19.0687 - acc: 0.0882 - val_loss: 80.6098 - val_acc: 0.0000e+00
Epoch 40450/50000
68/68 [==============================] - 0s 191us/step - loss: 20.3337 - acc: 0.1176 - val_loss: 80.3417 - val_a

68/68 [==============================] - 0s 299us/step - loss: 18.3793 - acc: 0.0735 - val_loss: 81.5733 - val_acc: 0.0000e+00
Epoch 40557/50000
68/68 [==============================] - 0s 249us/step - loss: 18.3399 - acc: 0.1029 - val_loss: 80.2162 - val_acc: 0.0000e+00
Epoch 40558/50000
68/68 [==============================] - 0s 297us/step - loss: 18.5532 - acc: 0.0735 - val_loss: 80.2368 - val_acc: 0.0000e+00
Epoch 40559/50000
68/68 [==============================] - 0s 279us/step - loss: 18.5922 - acc: 0.0882 - val_loss: 80.5862 - val_acc: 0.0000e+00
Epoch 40560/50000
68/68 [==============================] - 0s 338us/step - loss: 18.4181 - acc: 0.0735 - val_loss: 81.7022 - val_acc: 0.0000e+00
Epoch 40561/50000
68/68 [==============================] - 0s 337us/step - loss: 17.8476 - acc: 0.0441 - val_loss: 85.6415 - val_acc: 0.0000e+00
Epoch 40562/50000
68/68 [==============================] - 0s 352us/step - loss: 17.9221 - acc: 0.0735 - val_loss: 92.3378 - val_acc: 0.0588
Epoch 4

Epoch 40613/50000
68/68 [==============================] - 0s 293us/step - loss: 17.8423 - acc: 0.0588 - val_loss: 82.0781 - val_acc: 0.0000e+00
Epoch 40614/50000
68/68 [==============================] - 0s 279us/step - loss: 18.1118 - acc: 0.0735 - val_loss: 82.2808 - val_acc: 0.0000e+00
Epoch 40615/50000
68/68 [==============================] - 0s 352us/step - loss: 18.0656 - acc: 0.0882 - val_loss: 83.8116 - val_acc: 0.0000e+00
Epoch 40616/50000
68/68 [==============================] - 0s 352us/step - loss: 17.8716 - acc: 0.0882 - val_loss: 85.8116 - val_acc: 0.0000e+00
Epoch 40617/50000
68/68 [==============================] - 0s 293us/step - loss: 17.9440 - acc: 0.0441 - val_loss: 85.2785 - val_acc: 0.0000e+00
Epoch 40618/50000
68/68 [==============================] - 0s 293us/step - loss: 17.8408 - acc: 0.0441 - val_loss: 83.5261 - val_acc: 0.0000e+00
Epoch 40619/50000
68/68 [==============================] - 0s 279us/step - loss: 17.8458 - acc: 0.0588 - val_loss: 82.1964 - val_a